<a href="https://colab.research.google.com/github/FrancescoMorri/Simple-Evolution/blob/main/Main%26Data_Visualisation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [9]:
from matplotlib import rc
rc('animation', html='jshtml')

In [10]:
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import matplotlib.patches as patches
import matplotlib

import random
import numpy as np

In [11]:
class Blob(object):
    '''
    Main class of the program, each blob has a certain speed, vision and life. It needs to eat at least one food
    for round (it is editable). If, after LIFE steps the Blob hasn't found food it dies.
    If it finds more than a given amount of food (we check using the variable fed), it can reproduce.
    In that case the offspring inherits teh VISION, SPEED and LIFE of the parent, with a random possible 
    mutation. Each blob moves randomly and they all live on a toroid.
    '''
    VISION = 0.1 # starting vision
    SPEED = 0.08 # starting speed
    LIFE = 13 # starting life

    color = 'cyan'
    fed = 0  # will became true if it is fed
    steps = 0  # when it is == 9 the blob has finished its energy
    mov_prob = [0, 0, 0, 0]  # the prob with which the blob moves
    vision = 0

    def __init__(self, x, y, radius, heir=False, vis=0.1, spe=0.05, old_life=12):
        """
        Initialization of the blob:
        x = position x
        y = position y
        radius = radius
        It randomizes the probabilities of moving.
        If it is not the first generation the newborn will have a VISION and SPEED possibly different from the parent.
        """
        # self.generation = gen
        self.x = x
        self.y = y
        self.r = radius

        if heir:  # change in the heritage
            self.VISION = vis
            self.SPEED = spe

            # Change in SPEED
            p = random.randint(0, 100)
            if (p < 75):
                pass
            else:
                gen = float(random.randint(-250, 250)/10000.)  # 50% of the basic speed
                new_speed = self.SPEED + gen
                new_speed = max(0.0001, new_speed)
                self.SPEED = min(new_speed, 0.3)

            # Change in VISION
            p = random.randint(0, 100)
            if (p < 75):
                pass
            else:
                gen = float(random.randint(-500, 500)/10000.)  # 50% of the basic vision
                new_vision = self.VISION + gen
                new_vision = max(0.001, new_vision)
                self.VISION = min(new_vision, 0.6)

        # Moving Probabilities normalized
        for i in range(len(self.mov_prob)):
            self.mov_prob[i] = float(random.randint(0, 100)/100)
        s = sum(self.mov_prob)
        for i in range(len(self.mov_prob)):
            self.mov_prob[i] /= s

        # Life Calculator
        '''
        if (self.SPEED - spe > 0.005):
            self.LIFE = old_life - 1
        elif (self.SPEED - spe < -0.005):
            self.LIFE = old_life + 1

        if (self.VISION - vis > 0.025):
            self.LIFE = old_life - 1
        elif (self.VISION - vis < -0.025):
            self.LIFE = old_life + 1
        '''
        self.LIFE = 16 - (int((self.SPEED * 100)/2) + int(self.VISION * 10))


    def move(self):
        '''
        It just move the blob using its probabilities.
        '''
        p = float(random.randint(0, 100)/100)
        m = 0.05
        if (p < self.mov_prob[0]):  # moving right
            nx = (self.x + m) % 4.
            ny = self.y
        elif (p > self.mov_prob[0] and p < (self.mov_prob[0] + self.mov_prob[1])):  # moving left
            nx = (self.x - m) % 4.
            ny = self.y
        elif (p > (self.mov_prob[0] + self.mov_prob[1]) and p < (self.mov_prob[0] + self.mov_prob[1] + self.mov_prob[2])):  # moving up
            nx = self.x
            ny = (self.y + m) % 4.
        else:  # moving down
            nx = self.x
            ny = (self.y - m) % 4.
        self.x = nx
        self.y = ny
        self.steps += 1

    def food_check(self, food_map):
        '''
        Check in a circle of radius VISION if there is any food, if there is it moves there, else it just use its basic motion.
        '''
        for f in food_map:
            d = np.sqrt(((f[0]-self.x)**2 + (f[1]-self.y)**2))
            if (d <= self.VISION):
                self.x = f[0]
                self.y = f[1]
                self.steps += 1
                self.fed += 1
                food_map.remove(f)
                return False
        return True

    def color_change(self):
        '''
        The color of the blobs depends on their attributes.
        '''
        r = np.interp(self.VISION, [0.01, 0.6], [0, 1])
        b = np.interp(self.SPEED, [0.0001, 0.2], [0, 1])
        g = 0.
        self.color = (r, g, b)


In [12]:
def central_column(n_food, kind):
    '''
    kind = 0 -> Array
    kind = 1 -> coordinates
    '''
    if (kind == 0):
        foody = []
        for i in range(n_food):
            x = float(random.randint(100, 300)/100)
            y = float(random.randint(0, 400)/100)
            foody.append((x, y))
        return foody
    elif (kind == 1):
        x = float(random.randint(100, 300)/100)
        y = float(random.randint(0, 400)/100)
        return (x, y)


def islands(n_food, kind):
    '''
    kind = 0 -> Array
    kind = 1 -> coordinates
    '''
    if (kind == 0):   
        foody = []
        for i in range(int(n_food/2)):
            x = float(random.randint(0, 200)/100)
            y = float(random.randint(0, 200)/100)
            foody.append((x, y))
        for i in range(int(n_food/2)):
            x = float(random.randint(200, 400)/100)
            y = float(random.randint(200, 400)/100)
            foody.append((x, y))
        return foody
    elif (kind == 1):
        p = random.randint(0, 100)
        if (p <= 50):
            x = float(random.randint(0, 200)/100)
            y = float(random.randint(0, 200)/100)
        elif (p > 50):
            x = float(random.randint(200, 400)/100)
            y = float(random.randint(200, 400)/100)
        return (x, y)                       


def food_rand(n_food, kind):
    '''
    kind = 0 -> Array
    kind = 1 -> coordinates
    '''
    if (kind == 0):
        foody = []
        for i in range(n_food):
            x = float(random.randint(0, 400)/100)
            y = float(random.randint(0, 400)/100)
            foody.append((x, y))
        return foody
    elif (kind == 1):
        x = float(random.randint(0, 400)/100)
        y = float(random.randint(0, 400)/100)
        return (x, y)


In [21]:
def animate(i):
    global blobbi, food, pop
    props = dict(boxstyle='round', facecolor='wheat', alpha=0.5)
    data = []
    mean_life = 0
    ax1.clear()
    ax2.clear()
    ax1.set(xlim=(0, 4), ylim=(0, 4))
    ax2.set(xlim=(0.01, 0.6), ylim=(0.0001, 0.2))
    for f in food:
        square = patches.Rectangle(f, 0.018, 0.018, color='black')
        ax1.add_patch(square)

    for b in blobbi:
        b.color_change()
        mean_life += b.LIFE
        # if the blob is alive
        if (b.steps < b.LIFE):
            check = b.food_check(food)  # check for food near him
            if (check):
                b.move()  # if no food is found, next move
            circle = patches.Circle((b.x, b.y), b.r, color=b.color)
            ax1.add_patch(circle)
            #ax1.annotate(str(b.generation), xy=(b.x, b.y), fontsize=8, ha="center", va='center', color='black')

        # else, if the blob is death
        elif (b.steps >= b.LIFE):
            if (b.fed != 0):  # check if it has eaten
                b.fed = 0
                b.steps = 0
            else:  # else kill him
                blobbi.remove(b)

        # checking if the blob can make a babyblob
        if (b.fed >= 3):
            b.steps += 1  # maybe too harsh?
            b.fed = 0
            nx = b.x + float(random.randint(-50, 50)/100)
            ny = b.y + float(random.randint(-50, 50)/100)
            blobbi.append(Blob(nx, ny, 0.05, heir=True, vis=b.VISION, spe=b.SPEED, old_life=b.LIFE))
            continue

        data.append((b.VISION, b.SPEED, b.color[0], b.color[1], b.color[2]))

    if (len(blobbi) == 0):
        mean_life = 0
    else:
        mean_life /= len(blobbi)

    for f in range(REFRESH):
        food.append((food_rand(0, 1)))

    ax1.set_title('Step %.d (%.d blob left; %.d food left)' % (i, len(blobbi), len(food)))

    ax2.set_title('Population')
    ax2.set_xlabel('VISION')
    ax2.set_ylabel('SPEED')
    data_np = np.array(data)
    xs = data_np[:, 0]
    ys = data_np[:, 1]
    colors = [(d[2], d[3], d[4]) for d in data_np]
    V_x = [0.1, 0.1]
    V_y = [0, 3]
    S_x = [0, 3]
    S_y = [0.08, 0.08]
    ax2.grid()
    ax2.plot(V_x, V_y, color='black', alpha=0.5, label='Starting Vision')
    ax2.plot(S_x, S_y, color='black', alpha=0.5, label='Starting Speed')
    ax2.text(0.61, 0.83, "Mean Life: %.3f" % (mean_life), transform=ax2.transAxes, fontsize=14,
        verticalalignment='top', bbox=props)
    ax2.scatter(xs, ys, color=colors, label='blobs')
    ax2.legend()

    pop.append((len(food), len(blobbi), np.mean(xs), np.mean(ys), mean_life))

In [22]:
FOOD = 200
BLOBS = 50
REFRESH = 5

In [26]:
%%capture
fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,8))

blobbi = []
food = []
pop = []
for i in range(BLOBS):
    x = float(random.randint(0, 400)/100)
    y = float(random.randint(0, 400)/100)
    blobbi.append(Blob(x, y, 0.05))

food = food_rand(FOOD, kind=0)
counting = 0


In [24]:
anim = animation.FuncAnimation(fig, animate, interval=10, frames=100, blit=False, repeat=False)
data = np.array(pop)
#np.savetxt("/home/burrito/Documents/python/evolution/data/simulation3_c.csv", data, delimiter=',', fmt='%.8e')

In [25]:
anim